# Check funding rate entities

* Query positions to ensure `netFunding` is recorded properly
* Check `fundingRates` value on the entities for historical funding rate chart


In [1]:
import os
from copy import deepcopy
from datetime import datetime
import asyncio
import requests
import pandas as pd
import numpy as np
import json
from gql import Client, gql
from gql.transport.aiohttp import AIOHTTPTransport
from decimal import Decimal
from dotenv import load_dotenv
import plotly.io as pio
import plotly.express as px

load_dotenv()

pio.renderers.default = 'notebook'

In [2]:
## constants
INFURA_KEY = os.getenv('INFURA_KEY')

# mainnet
SUBGRAPH_ENDPOINT = 'https://api.thegraph.com/subgraphs/name/tburm/optimism-perps'
RPC_ENDPOINT = f'https://optimism-mainnet.infura.io/v3/{INFURA_KEY}'

# testnet
# SUBGRAPH_ENDPOINT = 'https://api.thegraph.com/subgraphs/name/kwenta/optimism-goerli-perps'
# RPC_ENDPOINT = f'https://optimism-kovan.infura.io/v3/{INFURA_KEY}'


In [3]:
# functions
convertDecimals = lambda x: Decimal(x) / Decimal(10**18)
convertBytes = lambda x: bytearray.fromhex(x[2:]).decode().replace('\x00', '')

def clean_df(df, decimal_cols=[], bytes_cols=[]):
    for col in decimal_cols:
        if col in df.columns:
            df[col] = df[col].apply(convertDecimals)
        else:
            print(f"{col} not in DataFrame")
    for col in bytes_cols:
        if col in df.columns:
            df[col] = df[col].apply(convertBytes)
        else:
            print(f"{col} not in DataFrame")
    return df

async def run_query(query, params, endpoint=SUBGRAPH_ENDPOINT):
    transport = AIOHTTPTransport(url=endpoint)

    async with Client(
        transport=transport,
        fetch_schema_from_transport=True,
    ) as session:

        # Execute single query
        query = query

        result = await session.execute(query, variable_values=params)
        df = pd.DataFrame(result)
        return df

async def run_recursive_query(query, params, accessor, endpoint=SUBGRAPH_ENDPOINT):
  transport = AIOHTTPTransport(url=endpoint)

  async with Client(
      transport=transport,
      fetch_schema_from_transport=True,
  ) as session:
    done_fetching = False
    all_results = []
    while not done_fetching:
      result = await session.execute(query, variable_values=params)
      if len(result[accessor]) > 0:
        all_results.extend(result[accessor])
        params['last_id'] = all_results[-1]['id']
      else:
        done_fetching = True
    
    df = pd.DataFrame(all_results)
    return df


In [4]:
position_query = gql("""
query positions(
    $last_id: ID!
  ) {
    futuresPositions(
      where: {
        id_gt: $last_id
      }
      first: 1000
     ) {
      id
      account
      asset
      initialMargin
      size
      entryPrice
      avgEntryPrice
      lastPrice
      exitPrice
      pnl
      pnlWithFeesPaid
      openTimestamp
      timestamp
      closeTimestamp
      feesPaid
      netFunding
      isLiquidated
      isOpen
      margin
      netTransfers
      totalDeposits
      totalVolume
    }  
}
""")

funding_query = gql("""
query funding(
    $last_id: ID!
  ) {
    fundingRateUpdates(
      where: {
        id_gt: $last_id
      }
      first: 1000
     ) {
      id
      timestamp
      market
      marketKey
      asset
      funding
      fundingRate
      sequenceLength
    }  
}
""")


### Run a query

In [5]:
position_params = {
    'last_id': ''
}

position_cols = [
    'avgEntryPrice',
    'entryPrice',
    'exitPrice',
    'feesPaid',
    'initialMargin',
    'lastPrice',
    'margin',
    'netFunding',
    'netTransfers',
    'pnl',
    'pnlWithFeesPaid',
    'size',
    'totalDeposits',
    'totalVolume'
]

position_bytes_cols = [
    'asset'
]

df_position = await run_recursive_query(position_query, position_params, 'futuresPositions')
df_position = df_position.replace({None: np.nan})
df_position = clean_df(df_position, decimal_cols=position_cols, bytes_cols=position_bytes_cols)


In [6]:
df_position

id  \
0        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x0   
1        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x1   
2       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x10   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x100   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x101   
...                                                 ...   
11382    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xb   
11383    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xc   
11384    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xd   
11385    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xe   
11386    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xf   

                                          account  asset  \
0      0x8feafd5e0fcefdd2624906c0f913d563306aae17  MATIC   
1      0x8feafd5e0fcefdd2624906c0f913d563306aae17  MATIC   
2      0xc8728ae130381eb77fc9a8b715564b00e83e19df  MATIC   
3      0x2c23f12195077bee4ac4f7d598af30904a5fbf91  MATIC   
4      0xd8e80c06f9f3a41c85cad28117e01ebd50fd535e  MATIC   
...                                           ...    ...   
11382  0x78f214cf1287b5c97df55a285e885b09c0d43e3d    XAG   
11383  0x88747e96c045e71b357ce0b75597492beaa1fb8f    XAG   
11384  0x11ba886f23173da913aa3dbc51492e8080a781ac    XAG   
11385  0x41dbd3a603adfb85c47fee7cf999d32bcc36a4f1    XAG   
11386  0xefabf4585217f458d54b6b5225a9c7a2222bd704    XAG   

                initialMargin size             entryPrice  \
0       77.199529739466510105    0                  1.336   
1       75.199529739466510105    0   1.340312948674674971   
2      197.498040648137408231    0   1.252917520139616653   
3                          98    0   1.271783672974139673   
4      777.321876625415779658    0   1.257577965021184482   
...                       ...  ...                    ...   
11382  162.739186100680223994    0  21.695059131724097826   
11383                      98    0  21.728833842533239428   
11384                    4998    0  21.482620917757409705   
11385  183.427032240973901673    0  21.728166360389986619   
11386                     588    0  20.818505592475501069   

               avgEntryPrice              lastPrice              exitPrice  \
0                      1.336   1.030985589554772303                    NaN   
1       1.340312948674674971   1.341738286882998216   1.341738286882998216   
2       1.252917520139616653   1.215543235997026069   1.215543235997026069   
3       1.271783672974139673   1.268341831466371221   1.268341831466371221   
4       1.257577965021184482   1.205252195554925268   1.205252195554925268   
...                      ...                    ...                    ...   
11382  21.695059131724097826  21.635837322225261266  21.635837322225261266   
11383  21.728833842533239428  21.580583270495936189  21.580583270495936189   
11384  21.482620917757409705   21.82713009230149882   21.82713009230149882   
11385  21.728166360389986619  21.816099329108998862  21.816099329108998862   
11386  20.818505592475501069   20.08498698104437367   20.08498698104437367   

                           pnl  ...   timestamp closeTimestamp  \
0                            0  ...  1678473564            NaN   
1         2.052092628903229758  ...  1675952960     1675952960   
2        29.769574101247450474  ...  1676274397     1676274397   
3         6.767650966258712392  ...  1677309680     1677309680   
4       210.365882266396886773  ...  1677358123     1677358123   
...                        ...  ...         ...            ...   
11382   -15.956808702549099059  ...  1676542759     1676542759   
11383   -13.642729241618423108  ...  1676587925     1676587925   
11384   641.506744317628356061  ...  1676883214     1676883214   
11385    14.574525202046228121  ...  1677033107     1677033107   
11386  -203.805505645917437276  ...  1678412441     1678412441   

                    feesPaid             netFunding isLiquidated isOpen  \
0                          0                      0        False   True   
1       7.

In [7]:
df_position.loc[df_position['netFunding'].abs() > 0, :]

id  \
1        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x1   
2       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x10   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x100   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x101   
5      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x102   
...                                                 ...   
11382    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xb   
11383    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xc   
11384    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xd   
11385    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xe   
11386    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xf   

                                          account  asset  \
1      0x8feafd5e0fcefdd2624906c0f913d563306aae17  MATIC   
2      0xc8728ae130381eb77fc9a8b715564b00e83e19df  MATIC   
3      0x2c23f12195077bee4ac4f7d598af30904a5fbf91  MATIC   
4      0xd8e80c06f9f3a41c85cad28117e01ebd50fd535e  MATIC   
5      0x20bffd797ef3460e0283800ca5039b1c30dc764e  MATIC   
...                                           ...    ...   
11382  0x78f214cf1287b5c97df55a285e885b09c0d43e3d    XAG   
11383  0x88747e96c045e71b357ce0b75597492beaa1fb8f    XAG   
11384  0x11ba886f23173da913aa3dbc51492e8080a781ac    XAG   
11385  0x41dbd3a603adfb85c47fee7cf999d32bcc36a4f1    XAG   
11386  0xefabf4585217f458d54b6b5225a9c7a2222bd704    XAG   

                 initialMargin size             entryPrice  \
1        75.199529739466510105    0   1.340312948674674971   
2       197.498040648137408231    0   1.252917520139616653   
3                           98    0   1.271783672974139673   
4       777.321876625415779658    0   1.257577965021184482   
5      2790.254775270753408915    0   1.257684245661669336   
...                        ...  ...                    ...   
11382   162.739186100680223994    0  21.695059131724097826   
11383                       98    0  21.728833842533239428   
11384                     4998    0  21.482620917757409705   
11385   183.427032240973901673    0  21.728166360389986619   
11386                      588    0  20.818505592475501069   

               avgEntryPrice              lastPrice              exitPrice  \
1       1.340312948674674971   1.341738286882998216   1.341738286882998216   
2       1.252917520139616653   1.215543235997026069   1.215543235997026069   
3       1.271783672974139673   1.268341831466371221   1.268341831466371221   
4       1.257577965021184482   1.205252195554925268   1.205252195554925268   
5       1.257684245661669336   1.160155168044309562   1.160155168044309562   
...                      ...                    ...                    ...   
11382  21.695059131724097826  21.635837322225261266  21.635837322225261266   
11383  21.728833842533239428  21.580583270495936189  21.580583270495936189   
11384  21.482620917757409705   21.82713009230149882   21.82713009230149882   
11385  21.728166360389986619  21.816099329108998862  21.816099329108998862   
11386  20.818505592475501069   20.08498698104437367   20.08498698104437367   

                           pnl  ...   timestamp closeTimestamp  \
1         2.052092628903229758  ...  1675952960     1675952960   
2        29.769574101247450474  ...  1676274397     1676274397   
3         6.767650966258712392  ...  1677309680     1677309680   
4       210.365882266396886773  ...  1677358123     1677358123   
5      -715.337868864416570932  ...  1677880355     1677880355   
...                        ...  ...         ...            ...   
11382   -15.956808702549099059  ...  1676542759     1676542759   
11383   -13.642729241618423108  ...  1676587925     1676587925   
11384   641.506744317628356061  ...  1676883214     1676883214   
11385    14.574525202046228121  ...  1677033107     1677033107   
11386  -203.805505645917437276  ...  1678412441     1678412441   

                    feesPaid              netFunding isLiquidated isOpen  \
1       7.861001237100389934       -8.08234215782E-7        False  False

In [8]:
df_position['pnl'].sum() + df_position['netFunding'].sum() - df_position['feesPaid'].sum()

Decimal('-2909603.549584949226258487')

In [9]:
df_position['feesPaid'].sum()

Decimal('973516.021494949648913009')

In [10]:
df_position['pnlWithFeesPaid'].sum()



Decimal('-2889539.549584949226258487')

## Historical funding rate

In [11]:
funding_params = {
    'last_id': ''
}

funding_decimal_cols = [
    'funding',
    'fundingRate'
]

funding_bytes_cols = [
    'marketKey',
    'asset'
]

df_funding = await run_recursive_query(funding_query, funding_params, 'fundingRateUpdates')
df_funding = df_funding.replace({None: np.nan})
df_funding = clean_df(df_funding, decimal_cols=funding_decimal_cols, bytes_cols=funding_bytes_cols)


In [12]:
df_funding['timestamp'] = df_funding['timestamp'].astype(np.int64)
df_funding['fundingRate'] = df_funding['fundingRate'].astype(np.float64)


In [13]:
df_funding

id   timestamp  \
0         0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-1  1675952475   
1        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-10  1675960087   
2       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-100  1676082221   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-1000  1676748461   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-1001  1676750878   
...                                                ...         ...   
80178    0xdcb8438c979fa030581314e5a5df42bbfed744a0-95  1677033107   
80179    0xdcb8438c979fa030581314e5a5df42bbfed744a0-96  1677033152   
80180    0xdcb8438c979fa030581314e5a5df42bbfed744a0-97  1677038477   
80181    0xdcb8438c979fa030581314e5a5df42bbfed744a0-98  1677177995   
80182    0xdcb8438c979fa030581314e5a5df42bbfed744a0-99  1677178010   

                                           market   marketKey  asset  \
0      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042  sMATICPERP  MATIC   
1      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042  sMATICPERP  MATIC   
2      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042  sMATICPERP  MATIC   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042  sMATICPERP  MATIC   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042  sMATICPERP  MATIC   
...                                           ...         ...    ...   
80178  0xdcb8438c979fa030581314e5a5df42bbfed744a0    sXAGPERP    XAG   
80179  0xdcb8438c979fa030581314e5a5df42bbfed744a0    sXAGPERP    XAG   
80180  0xdcb8438c979fa030581314e5a5df42bbfed744a0    sXAGPERP    XAG   
80181  0xdcb8438c979fa030581314e5a5df42bbfed744a0    sXAGPERP    XAG   
80182  0xdcb8438c979fa030581314e5a5df42bbfed744a0    sXAGPERP    XAG   

                     funding   fundingRate sequenceLength  
0                          0  0.000000e+00              1  
1           -1.9047554247E-8  1.699673e-07             10  
2      -0.001322592712477598  1.551538e-03            100  
3      -0.023724414029589254  5.880351e-04           1000  
4      -0.023747721570361566  5.330023e-04           1001  
...                      ...           ...            ...  
80178  -0.009786980809347932  1.269254e-04             95  
80179  -0.009788424095941762  1.269323e-04             96  
80180  -0.009959739826614255  1.277435e-04             97  
80181  -0.014718547604870155  1.489971e-04             98  
80182  -0.014719098872674958  1.489994e-04             99  

[80183 rows x 8 columns]

In [14]:
df_funding_sorted = df_funding.sort_values(['asset', 'timestamp'])


In [15]:
fig = px.line(
    df_funding_sorted,
    x='timestamp',
    y='fundingRate',
    color='asset'
)

fig.show()

## Look at a specific market

In [16]:
asset = 'APE'
last_price = df_position[(df_position['asset'] == asset)].sort_values('timestamp', ascending=False).iloc[0, :]['lastPrice']

df_position['sizeUsd'] = df_position.apply(lambda x: x['size'] * last_price, axis=1)
df_long = df_position.loc[(df_position['asset'] == asset) & (df_position['isOpen'] == True) & (df_position['size'] > 0), :].sort_values('size', ascending=False)
df_short = df_position.loc[(df_position['asset'] == asset) & (df_position['isOpen'] == True) & (df_position['size'] < 0), :].sort_values('size', ascending=True)

long_oi = df_long['size'].sum()
short_oi = abs(df_short['size'].sum())
total_oi = long_oi + short_oi

df_long['oiSide'] = df_long['size'].apply(lambda x: x / long_oi)
df_short['oiSide'] = df_short['size'].apply(lambda x: -1 * x / short_oi)
df_long['oiTotal'] = df_long['size'].apply(lambda x: x / total_oi)
df_short['oiTotal'] = df_short['size'].apply(lambda x: -1 * x / total_oi)

display_cols = [
    'account',
    'asset',
    'margin',
    'size',
    'sizeUsd',
    'oiSide',
    'oiTotal',
    'avgEntryPrice',
    'pnl',
    'totalVolume'
]

print(f'Long  OI: {round(df_long.sizeUsd.sum(), 2)}')
print(f'Short OI: {round(-df_short.sizeUsd.sum(), 2)}')


Long  OI: 306335.89
Short OI: 112869.60


In [17]:
df_long[display_cols]

account asset  \
10631  0x6662304e3198c8d54530fbdf02a869fa84537639   APE   
10635  0x65d674d359f3e79f16c1603c649855fe0564594b   APE   
10521  0x53bfd162c558f54446dd78ad86ff1450e47bc6a5   APE   
10494  0xf2eaeb6a0c248bcd69fd314180d69907b9be7491   APE   
10607  0xbb625947781b80179e79a47f373c7838111bf7d0   APE   
10611  0x34d88c6ecbdb1188e16655ea67468f6f072878ba   APE   
10622  0x554ed966ad76076a8c4dac4f3506b025e8c5bc24   APE   

                         margin                     size  \
10631  13826.406737506516954535               71321.3126   
10635   7136.278065855191990077  2480.836167020895753083   
10521   2639.952445324378805288                     1520   
10494   2052.832302103511403584                   1081.9   
10607    996.405255838147931688   505.330973949753708252   
10611    997.200540827270960814   253.240729850216946395   
10622     97.975915386111367637     5.125889067518149287   

                            sizeUsd                              oiSide  \
10631              283127.067480724      0.9242373396182611955195489480   
10635  9848.27456566953070684370842     0.03214861498547570172925150827   
10521                    6034.00480     0.01969734859057763635704195384   
10494                   4294.861706     0.01402010621062233208860769069   
10607  2006.03258052729528579629448    0.006548473912831845709853685376   
10611  1005.29985491560022078208730    0.003281691403415804429548015609   
10622    20.34844686688949795057538  0.00006642527881548416614819823476   

                                  oiTotal         avgEntryPrice  \
10631      0.6753896987031903019245562641  4.005511476204663455   
10635     0.02349271389287667534706859160  4.056376483090751166   
10521     0.01439390701887964494536413680  5.036993579894540444   
10494     0.01024524210771439991209832869  5.461113341734655219   
10607    0.004785320429468846656283437137  3.944801140397336933   
10611    0.002398107578195553764151702969  3.946142338566012791   
10622  0.00004854050699141311004819777942   3.91551812953650883   

                         pnl                totalVolume  
10631                      0  285678.336117280263990788  
10635                      0   10063.205486304560477212  
10521                      0     7656.23024143970147488  
10494  -0.483771589822483779   17724.651801678347960528  
10607                      0     1993.43020231508539037  
10611                      0     999.323965911298982951  
10622                      0      20.070511573860303316

In [18]:
df_short[display_cols]


account asset  \
10634  0x5a5670d2587815ddad5bba11dfc18ddc19bcff62   APE   
10467  0x000741def5c59bead2b2f6be2d35fc4145e39e6b   APE   
10632  0xbf1cfce65043191daa5f701398bc6d3112d47e29   APE   
10576  0x31304ccdd28e62ef552824db08a350d752068c39   APE   
10633  0x60fe5cbd886a778f584ffcc63833b068104d1f77   APE   
10479  0x653d99f0bdf3ea2587763afb9713fa948ba3b728   APE   
10630  0xbd8c54148233b886cfbc2179aa53e252e135b6fc   APE   
10613  0x3689ef967ce315af3b11ed1f3c9a96739cde2454   APE   
10625  0x61b81ca86dcb5ea9bf902b23ab1c3c5891bf94f4   APE   
10603  0x72924ef7048688503c620c67437b0c165ecdbd86   APE   
10638  0x03a46b7990ac95f5119caecd5178fc85beddcd2a   APE   

                         margin                    size  \
10634    4765.78594270205746429                   -9300   
10467  22980.444539902943025893                   -8050   
10632  19658.535682145147817039                   -7000   
10576   7398.897694348357068992              -1600.0909   
10633     993.82185016954434058                   -1300   
10479    616.180591500536014343               -868.9141   
10630     56.666362523749184996               -192.2633   
10613     50.682392183941486488                -66.6137   
10625     42.713285172428583291  -54.237157715766249398   
10603   7983.340100936214763591                   -0.37   
10638     42.644713539959829995                  -0.002   

                            sizeUsd                              oiSide  \
10634                  -36918.58200      0.3270905791691856571192620523   
10467                  -31956.40700      0.2831267916464456494419418839   
10632                  -27788.18000      0.2461972101273440429929929426   
10576               -6351.944849366     0.05627684507573586348032811017   
10633                   -5160.66200     0.04572233902364960798441297505   
10479               -3449.363059334     0.03056060389433029064394539557   
10630                -763.235312542    0.006762098295696655134453528573   
10613                -264.439069438    0.002342872442322836839531761997   
10625  -215.30741447058591088521652    0.001907576702122628936846579392   
10603                    -1.4688038  0.00001301328110673104227248676982   
10638                   -0.00793948    7.034206003638401228371226930E-8   

                                   oiTotal         avgEntryPrice  \
10634      0.08806798373393466973150425804  4.067483740673624733   
10467      0.07623088914604022487511927712   5.20635672168900354   
10632      0.06628772969220889119575589315    4.0086686456966666   
10576      0.01515234186602332110020273189  4.627410738214486123   
10633      0.01231057837141022265064038016  4.017451760053518674   
10479     0.008228334712364137957908307959  5.495160731119314059   
10630     0.001820671094304580815805282002  4.006249018288358494   
10613    0.0006308101341996993450638177628  3.973254451393050689   
10625    0.0005136082928480592816401327291  3.952164496684067831   
10603  0.000003503779998016755677489954352  3.823206677982224688   
10638     1.893935134063111177021596947E-8   5.08764417238680099   

                          pnl               totalVolume  
10634                       0    37827.5987882647100241  
10467                       0   41911.17160959647850905  
10632                       0     28060.680519876666203  
10576                       0   7404.277812779281493588  
10633                       0     5222.6872880695742762  
10479                       0    4774.82264103588076882  
10630  -36.044818906330123097   7878.595634044125497405  
10613                       0    264.673180048761260681  
10625                       0    214.354169125305725144  
10603  -28.957186946910797238  80340.661882803726191354  
10638  131.100336596999679327  66388.957995427530174007